**WARNING** This notebook produces videos of gameplay, and these videos sometimes have jittery, flashing colors in them. If you are sensitive to those kinds of videos, please be cautious.

This notebook uses imageio to create videos. You will need to install imageio and imageio-ffmpeg from pip for those cells to work.

In [2]:
%pylab inline
import torch
import sys, os
import pystk
import imageio
from IPython.display import Video, display

device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
print('device = ', device)

Populating the interactive namespace from numpy and matplotlib
device =  cuda


In [3]:
# This class initializes pystk -- Only create one instance!

class Rollout:
    def __init__(self, screen_width, screen_height, hd=True, render=True, track='lighthouse'):
        if render:
            if hd:
                config = pystk.GraphicsConfig.hd()
            else:
                config = pystk.GraphicsConfig.ld()
        else:
            config = pystk.GraphicsConfig.none()
        config.screen_width = screen_width
        config.screen_height = screen_height
        pystk.init(config)
        self.render = render
        race_config = pystk.RaceConfig(track=track)
        self.race = pystk.Race(race_config)
        self.race.start()
        
    def __call__(self, agent, n_steps=200):
        self.race.restart()
        self.race.step()
        
        data = []
        track_info = pystk.Track()
        track_info.update()
        
        for i in range(n_steps):
            world_info = pystk.WorldState()
            world_info.update()
            
            kart_info = world_info.players[0].kart
            
            agent_data = {'track_info': track_info, 'kart_info': kart_info}
            if self.render:
                # render_data[0].image has shape (screen_width, screen_height, 3)
                agent_data['image'] = np.array(self.race.render_data[0].image)
                
            action = agent(**agent_data)
            agent_data['action'] = action
            
            self.race.step(action)
            
            data.append(agent_data)
            
        return data

In [4]:
screen_width = 800
screen_height = 600

rollout = Rollout(screen_width, screen_height)

# This first agent just accelerates as fast as possible and never steers
def dummy_agent(**kwargs):
    action = pystk.Action()
    action.acceleration = 1
    return action

In [5]:
def show_video(frames, fps=30):
    imageio.mimwrite('/tmp/test.mp4', frames, fps=fps, bitrate=1_000_000)
    display(Video('/tmp/test.mp4', width=screen_width, height=screen_height, embed=True))
    
def show_agent(agent, **kwargs):
    data = rollout(agent, **kwargs)
    show_video([d['image'] for d in data])
    
# Visualize the first agent
show_agent(dummy_agent)

IMAGEIO FFMPEG_WRITER WARNING: input image is not divisible by macro_block_size=16, resizing from (800, 600) to (800, 608) to ensure video compatibility with most codecs and players. To prevent resizing, make your input image divisible by the macro_block_size or set the macro_block_size to 1 (risking incompatibility).


In [6]:
# This agent turns left in addition to accelerating, so that it can make it around that first turn.
def slightly_better_agent(**kwargs):
    action = pystk.Action()
    action.acceleration = 1
    action.steer = -0.6
    return action

show_agent(slightly_better_agent)

IMAGEIO FFMPEG_WRITER WARNING: input image is not divisible by macro_block_size=16, resizing from (800, 600) to (800, 608) to ensure video compatibility with most codecs and players. To prevent resizing, make your input image divisible by the macro_block_size or set the macro_block_size to 1 (risking incompatibility).


In [8]:
# This agent uses a more advanced controller to make it all the way around the track.

# Note that you won't be able to run this cell -- the controller it uses is hidden since you
# will need to implement one for homework 5.

from _auto_pilot import auto_pilot

show_agent(auto_pilot, n_steps=600)

IMAGEIO FFMPEG_WRITER WARNING: input image is not divisible by macro_block_size=16, resizing from (800, 600) to (800, 608) to ensure video compatibility with most codecs and players. To prevent resizing, make your input image divisible by the macro_block_size or set the macro_block_size to 1 (risking incompatibility).
